In [2]:
import torch
import torch.autograd as autograd         # computation graph
from torch import Tensor                  # tensor node in the computation graph
import torch.nn as nn                     # neural networks
import torch.optim as optim               # optimizers e.g. gradient descent, ADAM, etc.

import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
from mpl_toolkits.axes_grid1 import make_axes_locatable
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.ticker
from torch.nn.parameter import Parameter

import numpy as np
import time
from pyDOE import lhs         #Latin Hypercube Sampling
import scipy.io

from smt.sampling_methods import LHS
from scipy.io import savemat

#Set default dtype to float32
torch.set_default_dtype(torch.float)

#PyTorch random number generator
torch.manual_seed(1234)

# Random number generators in other libraries
np.random.seed(1234)

# Device configuration
device = torch.device('cuda:3' if torch.cuda.is_available() else 'cpu')

print(device)

if device == 'cuda': 
    print(torch.cuda.get_device_name())

    

cuda:3


In [3]:
lr_tune = np.array([0.05,0.1,0.25,0.5,1]).reshape(-1,1)
n_value = np.array([1.0,3.0,5.0,8.0,10.0]).reshape(-1,1)
r_value = np.array([2,6,8]).reshape(-1,1)

LR_tune,N_value,R_value = np.meshgrid(lr_tune,n_value,r_value)

LR_tune = LR_tune.flatten('F').reshape(-1,1)
N_value = N_value.flatten('F').reshape(-1,1)
R_value = R_value.flatten('F').reshape(-1,1)


lrnr_tune = np.hstack((LR_tune,N_value,R_value))

In [3]:
def true_1D_1(x): #True function for 1D_1 dy2/dx2 + dy/dx - 6y = 0; BC1: y(0)=2; BC2: dy/dx at (x=0) = -1;
    y = np.exp(2*x) + np.exp(-3*x)
    return y
    

In [4]:
loss_thresh = 0.005

x = np.linspace(0,2,100).reshape(-1,1)

bc1_x = x[0].reshape(-1,1)
bc1_y = true_1D_1(x[0]).reshape(-1,1)
x_bc1_train = torch.from_numpy(bc1_x).float().to(device)
y_bc1_train = torch.from_numpy(bc1_y).float().to(device)
    

bc2_x = x[0].reshape(-1,1)
x_bc2_train = torch.from_numpy(bc2_x).float().to(device)
bc2_val = torch.tensor(-1.0,device=device)
bc2_val = bc2_val.view(1,1)

x_test = x.reshape(-1,1)
x_test_tensor = torch.from_numpy(x_test).float().to(device)
y_true = true_1D_1(x_test)
y_true_norm = np.linalg.norm(y_true,2)

# Domain bounds
lb = np.array(x[0]) 
ub = np.array(x[-1]) 

In [5]:
def colloc_pts(N_f,seed):
    #Collocation Points
    # Latin Hypercube sampling for collocation points 
    # N_f sets of tuples(x,y)
    x01 = np.array([[0.0, 1.0]])
    sampling = LHS(xlimits=x01,random_state =seed)
    
    x_coll_train = lb + (ub-lb)*sampling(N_f)
    x_coll_train = np.vstack((x_coll_train, bc1_x.reshape(-1,1))) # append training points to collocation points 

    return x_coll_train

In [6]:
class Sequentialmodel(nn.Module):
    
    def __init__(self,layers,n_val,rowdy_terms):
        super().__init__() #call __init__ from parent class 
              
    
        self.activation = nn.Tanh()
        self.loss_function = nn.MSELoss(reduction ='mean')
        
        'Initialise neural network as a list using nn.Modulelist'  
        self.linears = nn.ModuleList([nn.Linear(layers[i], layers[i+1]) for i in range(len(layers)-1)])
        
        for i in range(len(layers)-1):
            nn.init.xavier_normal_(self.linears[i].weight.data, gain=1.0)
            # set biases to zero
            nn.init.zeros_(self.linears[i].bias.data) 
        
        
        self.omega1 = Parameter(torch.ones((len(layers)-2,1))) 
        self.omega1.requiresGrad = True
        
        
        self.alpha = Parameter(torch.zeros(rowdy_terms,len(layers)-2))
        self.alpha.requiresGrad = True
        
        self.omega = Parameter((1/n_val)*torch.ones(rowdy_terms,len(layers)-2))
        self.omega.requiresGrad = True
        
        self.n = torch.tensor(n_val)
    
    'forward pass'
    def forward(self,x):
        if torch.is_tensor(x) != True:         
            x = torch.from_numpy(x)                
        
        u_b = torch.from_numpy(ub).float().to(device)
        l_b = torch.from_numpy(lb).float().to(device)
                      
        #preprocessing input 
        x = (x - l_b)/(u_b - l_b) #feature scaling
        
        #convert to float
        a = x.float()
        
        for i in range(len(layers)-2):
            z = self.linears[i](a)
            a = self.activation(self.omega1[i,0]*z)
            for j in range(rowdy_terms):
                a = a + self.alpha[j,i]*self.n*torch.sin((j+1)*self.n*self.omega[j,i]*z)
            
        a = self.linears[-1](a) 
         
        return a
                        
    def loss_BC1(self,x,y):
                
        loss_bc1 = self.loss_function(self.forward(x), y)
                
        return loss_bc1
    
    def loss_BC2(self,x_bc2,bc2_val):
        g = x_bc2.clone()             
        g.requires_grad = True
        y = self.forward(g)    
            
        y_x = autograd.grad(y,g,torch.ones([x_bc2.shape[0], 1]).to(device), retain_graph=True, create_graph=True,allow_unused = True)[0]
        
        dy_dx = y_x[:,[0]]
        
        bc2 = dy_dx
        
        loss_bc2= self.loss_function(bc2,bc2_val)

        return loss_bc2
    
    def loss_PDE(self, x_coll,f_hat):
             
        g = x_coll.clone()             
        g.requires_grad = True
  
        y = self.forward(g) 

        y_x = autograd.grad(y,g,torch.ones([x_coll.shape[0], 1]).to(device), retain_graph=True, create_graph=True,allow_unused = True)[0]
        y_xx = autograd.grad(y_x,g,torch.ones(x_coll.shape).to(device), create_graph=True,allow_unused = True)[0]

        dy_dx = y_x[:,[0]]
        
        dy2_d2x = y_xx[:,[0]]
        
        f = dy2_d2x + dy_dx - 6*y
        
        loss_f = self.loss_function(f,f_hat)
                
        return loss_f
    
    
    def loss(self,x_bc1,y_bc1,x_bc2,bc2_val,x_coll,f_hat):

        loss_bc1 = self.loss_BC1(x_bc1,y_bc1)
        loss_bc2 = self.loss_BC2(x_bc2,bc2_val)
        loss_f = self.loss_PDE(x_coll,f_hat)
        
        loss_val = loss_bc1 + loss_bc2 + loss_f
        
        return loss_val
          
    'test neural network'
    
    def test(self):
        y_pred = self.forward(x_test_tensor)
        y_pred = y_pred.cpu().detach().numpy()

        return y_pred
    
    def test_loss(self):
        y_pred = self.test()
        
        test_mse = np.mean(np.square(y_pred.reshape(-1,1) - y_true.reshape(-1,1)))
        test_re = np.linalg.norm(y_pred.reshape(-1,1) - y_true.reshape(-1,1),2)/y_true_norm
        
        return test_mse, test_re

In [7]:
def train_step(x_coll,f_hat):
    def closure():
        optimizer.zero_grad()
        loss = PINN.loss(x_bc1_train,y_bc1_train,x_bc2_train,bc2_val,x_coll,f_hat)
        loss.backward()
        
        return loss

    optimizer.step(closure)

In [8]:
def data_update(loss_np):
    train_loss.append(loss_np)
    alpha_val.append(PINN.alpha.cpu().detach().numpy())
    omega_val.append(PINN.omega.cpu().detach().numpy())
    test_mse, test_re = PINN.test_loss()
    test_mse_loss.append(test_mse)
    test_re_loss.append(test_re)

In [9]:
def train_model(max_iter,rep):
    print(rep) 
    torch.manual_seed(rep*123)
    start_time = time.time()
    thresh_flag = 0
    nan_flag = 0
    for i in range(max_iter):
        x_coll = torch.from_numpy(colloc_pts(N_f,i*11)).float().to(device)
        f_hat = torch.zeros(x_coll.shape[0],1).to(device)
        train_step(x_coll,f_hat)
        
        loss_np = PINN.loss(x_bc1_train,y_bc1_train,x_bc2_train,bc2_val,x_coll,f_hat).cpu().detach().numpy()
        if(thresh_flag == 0):
            if(loss_np < loss_thresh):
                time_threshold[rep] = time.time() - start_time
                epoch_threshold[rep] = i+1            
                thresh_flag = 1       
        data_update(loss_np)
        print(i,"Train Loss",train_loss[-1],"Test MSE",test_mse_loss[-1],"Test RE",test_re_loss[-1])
        if(np.isnan(loss_np)):
            nan_flag =1
            print("NAN BREAK!")
            break
    
    elapsed_time[rep] = time.time() - start_time
    print('Training time: %.2f' % (elapsed_time[rep]))
    
    return nan_flag

In [10]:
nan_tune = []
for tune_reps in range(75):
    max_reps = 10
    max_iter = 100
    label = "1D_SODE_rowdy_tune"+str(tune_reps)

    N_f = 1000

    train_loss_full = []
    test_mse_full = []
    test_re_full = []
    alpha_full = []
    omega_full = []
    elapsed_time= np.zeros((max_reps,1))

    time_threshold = np.empty((max_reps,1))
    time_threshold[:] = np.nan
    epoch_threshold = max_iter*np.ones((max_reps,1))
    
    n_val = lrnr_tune[tune_reps,1]
    rowdy_terms = int(lrnr_tune[tune_reps,2])

    for reps in range(max_reps):

        train_loss = []
        test_mse_loss = []
        test_re_loss =[]
        alpha_val = []
        omega_val = []

        'Generate Training data'
        torch.manual_seed(reps*36)
         #Total number of collocation points 
        
        

        layers = np.array([1,50,50,50,50,50,50,50,50,50,1]) #9 hidden layers
        PINN = Sequentialmodel(layers,n_val,rowdy_terms)
        PINN.to(device)

        'Neural Network Summary'
        print(PINN)

        params = list(PINN.parameters())

        optimizer = torch.optim.LBFGS(PINN.parameters(), lr=lrnr_tune[tune_reps,0], 
                                  max_iter = 10, 
                                  max_eval = 15, 
                                  tolerance_grad = 1e-5, 
                                  tolerance_change = 1e-5, 
                                  history_size = 100, 
                                  line_search_fn = 'strong_wolfe')


        nan_flag = train_model(max_iter,reps)


        torch.save(PINN.state_dict(),label+'_'+str(reps)+'.pt')
        train_loss_full.append(train_loss)
        test_mse_full.append(test_mse_loss)
        test_re_full.append(test_re_loss)
        alpha_full.append(alpha_val)
        omega_full.append(omega_val) 
        
        if(nan_flag == 1):
            nan_tune.append(tune_reps)
            break

        print('Training time: %.2f' % (elapsed_time[reps]))

    mdic = {"train_loss": train_loss_full,"test_mse_loss": test_mse_full, "test_re_loss": test_re_full, "Time": elapsed_time, "alpha": alpha_full, "omega": omega_full, "label": label}
    savemat(label+'.mat', mdic)

Sequentialmodel(
  (activation): Tanh()
  (loss_function): MSELoss()
  (linears): ModuleList(
    (0): Linear(in_features=1, out_features=50, bias=True)
    (1): Linear(in_features=50, out_features=50, bias=True)
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): Linear(in_features=50, out_features=50, bias=True)
    (4): Linear(in_features=50, out_features=50, bias=True)
    (5): Linear(in_features=50, out_features=50, bias=True)
    (6): Linear(in_features=50, out_features=50, bias=True)
    (7): Linear(in_features=50, out_features=50, bias=True)
    (8): Linear(in_features=50, out_features=50, bias=True)
    (9): Linear(in_features=50, out_features=1, bias=True)
  )
)
0
0 Train Loss 4.3485093 Test MSE 386.2417625136802 Test RE 1.0018257671524593
1 Train Loss 3.9259238 Test MSE 387.29696673002445 Test RE 1.0031933170214795
2 Train Loss 2.9272954 Test MSE 386.8783487055908 Test RE 1.0026510092045016
3 Train Loss 2.393413 Test MSE 384.0392906967878 Test RE 0.998965320

97 Train Loss 2.3811698 Test MSE 383.8142556565999 Test RE 0.9986725968334939
98 Train Loss 2.3811698 Test MSE 383.8142556565999 Test RE 0.9986725968334939
99 Train Loss 2.3811698 Test MSE 383.8142556565999 Test RE 0.9986725968334939
Training time: 25.88
Training time: 25.88
Sequentialmodel(
  (activation): Tanh()
  (loss_function): MSELoss()
  (linears): ModuleList(
    (0): Linear(in_features=1, out_features=50, bias=True)
    (1): Linear(in_features=50, out_features=50, bias=True)
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): Linear(in_features=50, out_features=50, bias=True)
    (4): Linear(in_features=50, out_features=50, bias=True)
    (5): Linear(in_features=50, out_features=50, bias=True)
    (6): Linear(in_features=50, out_features=50, bias=True)
    (7): Linear(in_features=50, out_features=50, bias=True)
    (8): Linear(in_features=50, out_features=50, bias=True)
    (9): Linear(in_features=50, out_features=1, bias=True)
  )
)
1
0 Train Loss 4.322978 Te

92 Train Loss 2.3814385 Test MSE 383.78851394708005 Test RE 0.9986391067135101
93 Train Loss 2.3814385 Test MSE 383.78851394708005 Test RE 0.9986391067135101
94 Train Loss 2.3814385 Test MSE 383.78851394708005 Test RE 0.9986391067135101
95 Train Loss 2.3814385 Test MSE 383.78851394708005 Test RE 0.9986391067135101
96 Train Loss 2.3814385 Test MSE 383.78851394708005 Test RE 0.9986391067135101
97 Train Loss 2.3814385 Test MSE 383.78851394708005 Test RE 0.9986391067135101
98 Train Loss 2.3814385 Test MSE 383.78851394708005 Test RE 0.9986391067135101
99 Train Loss 2.3814385 Test MSE 383.78851394708005 Test RE 0.9986391067135101
Training time: 22.06
Training time: 22.06
Sequentialmodel(
  (activation): Tanh()
  (loss_function): MSELoss()
  (linears): ModuleList(
    (0): Linear(in_features=1, out_features=50, bias=True)
    (1): Linear(in_features=50, out_features=50, bias=True)
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): Linear(in_features=50, out_features=50, bias

88 Train Loss 1.9055643 Test MSE 302.599795750254 Test RE 0.8867412215732131
89 Train Loss 1.8960212 Test MSE 300.1839355125989 Test RE 0.8831943986935008
90 Train Loss 1.8814926 Test MSE 296.92907385559744 Test RE 0.8783931581435984
91 Train Loss 1.8609061 Test MSE 294.3246342490257 Test RE 0.8745323698253051
92 Train Loss 1.8338258 Test MSE 289.77300263710885 Test RE 0.8677438473260672
93 Train Loss 1.8230498 Test MSE 287.50330805928525 Test RE 0.8643387935428167
94 Train Loss 1.8034902 Test MSE 282.360852273268 Test RE 0.8565738750786637
95 Train Loss 1.749575 Test MSE 275.7564278505409 Test RE 0.846496963982333
96 Train Loss 1.7157106 Test MSE 271.6399126740222 Test RE 0.8401549173522591
97 Train Loss 1.7079368 Test MSE 269.4591544827611 Test RE 0.8367756886423907
98 Train Loss 1.698092 Test MSE 265.77848692656386 Test RE 0.831041084807141
99 Train Loss 1.6955639 Test MSE 264.62070328882817 Test RE 0.829229019586885
Training time: 115.50
Training time: 115.50
Sequentialmodel(
  (ac

84 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
85 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
86 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
87 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
88 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
89 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
90 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
91 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
92 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
93 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
94 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
95 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.9986116351678962
96 Train Loss 2.3807323 Test MSE 383.7673989745561 Test RE 0.998

...

4 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
5 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
6 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
7 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
8 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
9 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
10 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
11 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
12 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
13 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
14 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
15 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
16 Train Loss 4.8918943 Test MSE 383.353534890477 Test RE 0.9980730263956001
17 Tr

1 Train Loss 2.762874 Test MSE 380.3013137460455 Test RE 0.9940918090113285
2 Train Loss 2.3690214 Test MSE 379.3324046725831 Test RE 0.9928246574033623
3 Train Loss 2.3397527 Test MSE 376.22749142186206 Test RE 0.9887530722401633
4 Train Loss 2.312987 Test MSE 368.8006161283185 Test RE 0.978945245564963
5 Train Loss 2.2763047 Test MSE 364.58467234438206 Test RE 0.9733337568603309
6 Train Loss 2.2411194 Test MSE 360.58141107998495 Test RE 0.9679752420958032
7 Train Loss 2.2239084 Test MSE 354.0333828129494 Test RE 0.9591459336877145
8 Train Loss 2.1260908 Test MSE 336.11985300549304 Test RE 0.9345653283551385
9 Train Loss 2.1070695 Test MSE 334.3553134393926 Test RE 0.9321089909978184
10 Train Loss 2.0484986 Test MSE 320.7757664336598 Test RE 0.9129844027347854
11 Train Loss 1.9833381 Test MSE 311.98820687246376 Test RE 0.9003920910474011
12 Train Loss 1.9582512 Test MSE 309.6367110480764 Test RE 0.8969924867779994
13 Train Loss 1.9385741 Test MSE 306.07345259901695 Test RE 0.891816316

0 Train Loss 4.6863394 Test MSE 383.89676215281156 Test RE 0.9987799307169799
1 Train Loss 3.185163 Test MSE 382.6295383626659 Test RE 0.997130107084467
2 Train Loss 2.4552808 Test MSE 383.167536136606 Test RE 0.9978308702063502
3 Train Loss 2.367785 Test MSE 376.2344844767497 Test RE 0.9887622613246034
4 Train Loss 2.3523996 Test MSE 374.118795304432 Test RE 0.9859782757082982
5 Train Loss 2.3182156 Test MSE 369.6160181587997 Test RE 0.9800268506085469
6 Train Loss 2.3042035 Test MSE 368.8167436063215 Test RE 0.9789666497392348
7 Train Loss 2.2627318 Test MSE 361.8670590003143 Test RE 0.9696993576520785
8 Train Loss 2.2124338 Test MSE 353.823665322918 Test RE 0.958861808680076
9 Train Loss 2.186188 Test MSE 349.76183772188756 Test RE 0.9533421472533767
10 Train Loss 2.164951 Test MSE 345.8973727009998 Test RE 0.9480608529332788
11 Train Loss 2.1510036 Test MSE 343.21455088799974 Test RE 0.9443770587820332
12 Train Loss 2.1427088 Test MSE 341.6094671149899 Test RE 0.9421662249832683
13

21 Train Loss 1.9570316 Test MSE 308.8876323625532 Test RE 0.8959068196070439
22 Train Loss 1.94071 Test MSE 306.1402018217587 Test RE 0.8919135557797727
23 Train Loss 1.9187049 Test MSE 301.81074733008745 Test RE 0.8855843495565245
24 Train Loss 1.9116256 Test MSE 299.712745660741 Test RE 0.8825009643980711
25 Train Loss 1.8856498 Test MSE 296.8080801067045 Test RE 0.8782141744743985
26 Train Loss 1.845339 Test MSE 287.90870949047206 Test RE 0.8649479704409931
27 Train Loss 1.7815081 Test MSE 277.21562221012704 Test RE 0.8487336731341768
28 Train Loss 1.7510102 Test MSE 276.5424766328595 Test RE 0.847702583036172
29 Train Loss 1.7380465 Test MSE 272.49065196709483 Test RE 0.8414695143878991
30 Train Loss 1.7038578 Test MSE 263.06871268347425 Test RE 0.8267937449224908
31 Train Loss 1.6870198 Test MSE 263.39285093349696 Test RE 0.8273029521435107
32 Train Loss 1.6664629 Test MSE 260.27586967823265 Test RE 0.8223932473308344
33 Train Loss 1.6505295 Test MSE 256.5896393660711 Test RE 0.8

16 Train Loss 2.16089 Test MSE 345.35838507924745 Test RE 0.9473219165880624
17 Train Loss 2.1489735 Test MSE 342.5866639341107 Test RE 0.9435128275348543
18 Train Loss 2.1410394 Test MSE 341.34419177297264 Test RE 0.9418003364004439
19 Train Loss 2.1333458 Test MSE 341.19257271900716 Test RE 0.9415911476406323
20 Train Loss 2.1231363 Test MSE 338.4105237204531 Test RE 0.9377444717575332
21 Train Loss 2.1081252 Test MSE 334.6841477390956 Test RE 0.9325672371658489
22 Train Loss 2.0826664 Test MSE 328.4251004333913 Test RE 0.9238059460125003
23 Train Loss 2.0588813 Test MSE 325.1600544366809 Test RE 0.9192024565471449
24 Train Loss 2.0450742 Test MSE 325.02420980324723 Test RE 0.9190104253249437
25 Train Loss 2.0428796 Test MSE 325.50030326184265 Test RE 0.9196832594267406
26 Train Loss 2.0292184 Test MSE 321.87240087712826 Test RE 0.9145436787130156
27 Train Loss 2.0089784 Test MSE 318.74292867677616 Test RE 0.9100868974996082
28 Train Loss 1.9995534 Test MSE 316.8733010990583 Test RE 

In [14]:
lrnr_tune[tune_reps,2]

8.0

In [15]:
import scipy.io as sio

In [17]:
for tune_reps in range(75):
    label = "1D_SODE_rowdy_tune"+str(tune_reps)+".mat" 
    data = sio.loadmat(label)
    re = np.array(data["test_re_loss"])
    print(tune_reps," ",np.mean(re[:,-1]))

0   0.9324389206545124
1   0.5848853617125656
2   0.537285849030004
3   0.4257517991395723
4   0.3773328804977455
5   0.8909510921605175
6   0.8750549066548938
7   0.5079528642659948
8   0.48463803002166495
9   0.4876659147239414
10   [[1.00219243 1.00251906 0.9986913  0.99871131 0.99898183 0.99899581
  0.99907238 0.99863246 0.99858121 0.99856045 0.99855922 0.99855729
  0.9985561  0.99855392 0.99855268 0.99855268 0.99855268        nan]]
11   [[1.00265017 1.00166366 0.99870598 0.99762229 0.9985589  0.99874572
  0.99875185 0.99875309 0.99875454 0.99875552 0.99875677 0.99875766
  0.99875893 0.99875982 0.99876122 0.99876195 0.99871908 0.99868553
  0.99867527 0.99866763 0.99865756 0.99864873 0.99843971 0.99841379
  0.99841126 0.99840969 0.99840896 0.99840902 0.99840992 0.99841175
  0.99841465 0.99841866 0.99842379 0.99842972 0.99843657 0.99846814
  0.99831333 0.99823045 0.99822258 0.99821811 0.99821201 0.99820691
  0.99820691        nan]]
12   0.27885837784597367
13   0.18334601117218768
14

In [4]:
lrnr_tune[12]

array([0.25, 5.  , 2.  ])